In [1]:
import torch
import os
import torchvision.transforms as transforms
import matplotlib.pyplot as plt
from PIL import Image
import numpy as np
import cv2
import matplotlib.cm as cm
from einops import rearrange
repo = "isl-org/ZoeDepth"
# Zoe_N
model_zoe_n = torch.hub.load(repo, "ZoeD_N", pretrained=True)
device = "cuda" if torch.cuda.is_available() else "cpu"
model = model_zoe_n.to(DEVICE)

Using cache found in C:\Users\胡逸飞/.cache\torch\hub\isl-org_ZoeDepth_main


img_size [384, 512]


Using cache found in C:\Users\胡逸飞/.cache\torch\hub\intel-isl_MiDaS_master
D:\SubDiffusion\venv\lib\site-packages\torch\functional.py:504: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at ..\aten\src\ATen\native\TensorShape.cpp:3484.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]


Params passed to Resize transform:
	width:  512
	height:  384
	resize_target:  True
	keep_aspect_ratio:  True
	ensure_multiple_of:  32
	resize_method:  minimal
Using pretrained resource url::https://github.com/isl-org/ZoeDepth/releases/download/v1.0/ZoeD_M12_N.pt
Loaded successfully


In [44]:
image = Image.open('7.jpg')
# 调整图像到正方形
max_size = 960
if image.size[0] > image.size[1]:
    wpercent = max_size / float(image.size[0])
    hsize = int((float(image.size[1]) * float(wpercent)))
    image = image.resize((max_size, hsize), Image.Resampling.BILINEAR)
else:
    hpercent = max_size / float(image.size[1])
    wsize = int((float(image.size[0]) * float(hpercent)))
    image = image.resize((wsize, max_size), Image.Resampling.BILINEAR)

    # 创建一个n1*n1的纯黑色图像
    background = Image.new('RGB', (960, 960), (0, 0, 0))

# 计算输入图像在背景图像中的位置
bg_w, bg_h = background.size
img_w, img_h = image.size
offset = ((bg_w - img_w) // 2, (bg_h - img_h) // 2)

# 将输入图像放在背景图像中
background.paste(image, offset)
input_image=np.array(background)

# 将图像转换为张量
#input_image = transforms.ToTensor()(background).unsqueeze(0).to(device)
image_depth = input_image
with torch.no_grad():
    image_depth = torch.from_numpy(image_depth).float().to(device)
    image_depth = image_depth / 255.0
    image_depth = rearrange(image_depth, 'h w c -> 1 c h w')
    depth = model.infer(image_depth)

    depth = depth[0, 0].cpu().numpy()

    vmin = np.percentile(depth, 2)
    vmax = np.percentile(depth, 85)

    depth -= vmin
    depth /= vmax - vmin
    depth = 1.0 - depth
    depth_image = (depth * 255.0).clip(0, 255).astype(np.uint8)
cv2.imwrite('depth_image.png', depth_image)

True

True